In [1]:
import folium
import pandas as pd
google_tile = folium.TileLayer(tiles = 'https://mt1.google.com/vt/lyrs=y&x={x}&y={y}&z={z}', attr = 'Powered by Google', name='Google', overlay=False, control=False)
m = folium.Map(location=[7.94, 1.02], zoom_start=6, tiles=None) # no tiles to add the google map 
google_tile.add_to(m);

In [2]:
from branca.element import MacroElement
from jinja2 import Template

# custom macro element class for the color_map and choropleth layer binding
# thanks to stackoverflow answer https://stackoverflow.com/questions/74512212/how-to-hide-python-folium-choropleth-legend
class BindColormap(MacroElement):
    """Binds a colormap to a given layer.

    Parameters
    ----------
    colormap : branca.colormap.ColorMap
        The colormap to bind.
    """
    def __init__(self, layer, colormap):
        super(BindColormap, self).__init__()
        self.layer = layer
        self.colormap = colormap
        self._template = Template(u"""
        {% macro script(this, kwargs) %}
            {{this.colormap.get_name()}}.svg[0][0].style.display = 'block';
            {{this._parent.get_name()}}.on('overlayadd', function (eventLayer) {
                if (eventLayer.layer == {{this.layer.get_name()}}) {
                    {{this.colormap.get_name()}}.svg[0][0].style.display = 'block';
                }});
            {{this._parent.get_name()}}.on('overlayremove', function (eventLayer) {
                if (eventLayer.layer == {{this.layer.get_name()}}) {
                    {{this.colormap.get_name()}}.svg[0][0].style.display = 'none';
                }});
        {% endmacro %}
        """)  # noqa

In [3]:
regions = 'ghana_regions.geojson'
districts = 'ghana_districts.geojson'
df = pd.read_csv('gha_adminboundaries_tabulardata.csv')

#folium.GeoJson(regions, name="regions").add_to(m)
#folium.GeoJson(districts, name="districts").add_to(m)

cr = folium.Choropleth(
    geo_data=regions,
    name="regions",
    data=df,
    columns=["admin1Pcode", "region_value"],
    key_on="feature.properties.ADM1_PCODE",
    fill_color="YlGn",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Percentage(%) of fully vaccinated per region"
)

for key in cr._children:
    if key.startswith('color_map'):
        branca_color_map_cr = cr._children[key]
        del(cr._children[key])

for s in cr.geojson.data['features']:
    region_code = s['properties']['ADM1_PCODE']
    s['properties']['region'] = s['properties']['ADM1_EN']
    s['properties']['fully vaccinated (%)'] = float(df[df['admin1Pcode']==region_code]['region_value'].unique())

cr.geojson.add_child(
    folium.features.GeoJsonTooltip(['region', 'fully vaccinated (%)'], labels=True)
)

In [4]:

cs = folium.Choropleth(
    geo_data=districts,
    name="districts",
    data=df,
    columns=["admin2Pcode", "district_value"],
    key_on="feature.properties.ADM2_PCODE",
    fill_color="PuBu",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Percentage(%) of fully vaccinated per district",
)

for key in cs._children:
    if key.startswith('color_map'):
        branca_color_map_cs = cs._children[key]
        del(cs._children[key])

for s in cs.geojson.data['features']:
    district_code = s['properties']['ADM2_PCODE']
    s['properties']['district'] = s['properties']['ADM2_EN'] 
    s['properties']['fully vaccinated (%)'] = round(df[df['admin2Pcode']==district_code]['district_value'].squeeze(),2)

cs.geojson.add_child(
    folium.features.GeoJsonTooltip(['district', 'fully vaccinated (%)'], labels=True)
);

In [5]:
import pandas as pd
hc = pd.read_csv('2020_health_facilities_ghana.csv')
# hc.head(3)
# hc.shape
# print(hc['Type'].unique())

In [6]:
# let's exclude health care centers which perform special functions
exclusion_criteria = ['Maternity Home', 'RCH', 'Training Institution', 'Municipal Health Directorate', 'District Health Directorate',
'Regional Health Directorate', 'Municipal  Health Directorate', 'DHD', 'Psychiatric Hospital', 'Research Institution', 'Others']

In [7]:
hc = hc[~hc['Type'].isin(exclusion_criteria)]
hc.shape;

In [8]:
# drop health centers without coordinates information 
hc = hc[~hc['Latitude'].isna() & ~hc['Longitude'].isna()]
hc.shape;

In [9]:
# let's exclude also centers that do not belong to the government
hc = hc[hc['Ownership']=='Government']
hc.shape;

In [10]:
regions = list(df[df['region_value']<=50]['admin1Name_en'].unique())
regions;

In [11]:
# select only centers that have % of fully vaccinated per region below 50%
# hc['Region'].unique()
hc = hc[hc['Region'].isin(regions)]

In [38]:
from sklearn.model_selection import train_test_split

# we will aim for 31 centers in each arm, considering the stratification: 
out_experiment, in_experiment = train_test_split(hc, test_size=0.07, random_state=42, stratify=hc['Region']);
in_experiment.shape;

# we will split those in 3 groups
remain, control = train_test_split(in_experiment, test_size=0.33, random_state=42, stratify=in_experiment[['Region']]);
treatment_2, treatment_1 = train_test_split(remain, test_size=0.5, random_state=42, stratify=remain[['Region']]);


In [13]:
groups = {'control': [control, 'lightgray'], 'treatment_1': [treatment_1, 'beige'], 'treatment_2': [treatment_2, 'purple']}
for i in groups.items():
    group = folium.FeatureGroup(name=f'{i[0]}') 
    i[1][0].apply(lambda row:folium.Marker(location=[row["Latitude"], row["Longitude"]], tooltip=row['FacilityName'], icon=folium.Icon(color=i[1][1], icon="plus", prefix='fa')).add_to(group), axis=1);
    group.add_to(m)
    
m.add_child(cr)
m.add_child(cs)
m.add_child(folium.map.LayerControl())
m.add_child(branca_color_map_cr)
m.add_child(BindColormap(cr, branca_color_map_cr))
m.add_child(branca_color_map_cs)
m.add_child(BindColormap(cs, branca_color_map_cs))

# display the map 
m

**Figure 1**. Leveraging the healthwork force to increase covid19 vaccine uptake in Ghana. An RCT interactive design. 

In [15]:
m.save('ghana_deta/templates/map.html')